In [1]:
import numpy as np
import cv2

from scipy import ndimage as ndi
from matplotlib import pyplot as plt
from matplotlib import image as mpimage
import matplotlib as mpl
%matplotlib widget 

from os import listdir, walk
from os.path import isfile, join
# from numba import jit
# from numba.core.errors import NumbaWarning
import warnings


# warnings.simplefilter('ignore', category=NumbaWarning)
import ipywidgets as widgets

import time
import os
from pathlib import Path
import datetime
import random
import json

In [2]:
def show(img): # JIT NOT NEEDED
    plt.figure()
    plt.imshow(img[..., ::-1])
    return 0

def save_energies(energies, path):
    energies = energies.astype('float64')
    energies *= (255.0/energies.max())
    plt.imsave(path, energies, cmap='viridis')
    
def combine_image_and_mask(img, mask):
    d3dmask = np.stack((mask,)*3, axis=-1).astype('int64')
    return np.multiply(img, d3dmask)
    

def show_energies(img): # JIT NOT NEEDED
    plt.figure()
    plt.imshow(img)
    return 0

In [3]:
def kmeans(img, clusters): # BGR image JIT NOT NEEDED
    pixels = img.reshape((-1, 3))
    pixels = np.float32(pixels)
    criteria = (cv2.TERM_CRITERIA_EPS + cv2.TERM_CRITERIA_MAX_ITER, 10, 1.0)
    compactness, labels, centers = cv2.kmeans(pixels, clusters, None, criteria, 
            10, cv2.KMEANS_RANDOM_CENTERS)
    centers = np.uint8(centers)
    result = centers[labels.flatten()].reshape((img.shape))
    return result

In [4]:
def gray(img): # JIT NOT NEEDED
    if img.size == 0:
        return np.array([])
    return cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)

In [5]:
def backward_energy(img): # JIT NOT NEEDED
    rgbx = ndi.convolve1d(img, np.array([1, 0, -1]), axis=1, mode='wrap')
    rgby = ndi.convolve1d(img, np.array([1, 0, -1]), axis=0, mode='wrap')
    
    rgbx = np.sum(rgbx**2, axis=2)
    rgby = np.sum(rgby**2, axis=2)
    
    return np.sqrt(rgbx + rgby)

In [6]:
def forward_energy(img):
    height = img.shape[0]
    width = img.shape[1]
    # print(img)
    I = gray(img)
    energy = np.zeros((height, width))
    m = np.zeros((height, width))
    U = np.roll(I, 1, axis=0)
    L = np.roll(I, 1, axis=1)
    R = np.roll(I, -1, axis=1)

    cU = np.abs(R - L)
    cL = np.abs(U - L) + cU
    cR = np.abs(U - R) + cU
    
    for i in range(1, height):
        mU = m[i-1]
        mL = np.roll(mU, 1)
        mR = np.roll(mU, -1)
        
        mULR = np.array([mU, mL, mR])
        cULR = np.array([cU[i], cL[i], cR[i]])
        mULR += cULR

        argmins = np.argmin(mULR, axis=0)
        m[i] = np.choose(argmins, mULR)
        energy[i] = np.choose(argmins, cULR)
        
    return energy

In [7]:
def get_seam(img, energy_function):
    height, width = img.shape[:2]
    energies = energy_function(img)
    back = np.zeros_like(energies, dtype=np.int64)
    for i in range(1, height):
        for j in range(width):
            if j == 0:
                nei = np.argmin(energies[i - 1, j:j + 2])
                back[i, j] = nei + j
                me = energies[i - 1, nei + j]
            else:
                nei = np.argmin(energies[i - 1, j - 1:j + 2])
                back[i, j] = nei + j - 1
                me = energies[i - 1, nei + j - 1]
            energies[i, j] += me
    seam = []
    mask = np.ones((height, width), dtype=bool)
    j = np.argmin(energies[-1])
    for i in range(height - 1, -1, -1):
        mask[i, j] = False
        seam.append(j)
        j = back[i, j]
    seam.reverse()
    return np.array(seam), mask

In [8]:
def remove_seam(img, mask):
    height, width = img.shape[:2]
    mask3 = np.stack([mask] * 3, axis=2)
    return img[mask3].reshape((height, width - 1, 3))

In [9]:
def seam_carve_remove(img, perc, energy_function):
    for i in range(img.shape[1] * perc // 100):
        img = remove_seam(img, get_seam(img, energy_function)[1])
    return img

def fast_seam_carve_remove(img, perc, energy_function, vspace, hspace):
    for i in range(img.shape[1] * perc // 100):
        img = remove_seam(img, fast_get_seam(img, vspace, hspace, energy_function)[1])
    return img

def kmeans_fast_seam_carve_remove(img, perc, energy_function, clusters, vspace, hspace):
    kimg = kmeans(img, clusters)
    for i in range(img.shape[1] * perc // 100):
        seam = fast_get_seam(kimg, vspace, hspace, energy_function)[1]
        img = remove_seam(img, seam)
        kimg = remove_seam(kimg, seam)
    return img


In [10]:
def seam_carve_add(img, perc, energy_function):
    or_img = np.copy(img)
    rem = np.zeros_like(img, dtype=np.int64)
    # print(delmask)
    for i in range(img.shape[0]):
        for j in range(img.shape[1]):
            rem[i][j][0] = j
    # show(rem)
    nops = img.shape[1] * perc // 100
    for i in range(nops):
        mask = get_seam(img, energy_function)[1]
        img = remove_seam(img, mask)
        rem = remove_seam(rem, mask)
    out_img = np.empty((or_img.shape[0], or_img.shape[1] + nops, 3), dtype=np.int64)
    delmask = np.ones_like(or_img[:,:,0], dtype=np.bool8)
    # print(delmask.shape)
    # show(rem)
    cnt = 0
    for i in range(or_img.shape[0]):
        cnt = 0
        for j in rem[i, :, 0]:
            cnt += 1
            delmask[i][j] = False
        # print(i, cnt)
    for i in range(or_img.shape[0]):
        ptr = 0
        for j in range(or_img.shape[1]):
            # print(ptr)
            out_img[i][ptr] = or_img[i][j]
            ptr += 1
            if delmask[i][j] == True:
                out_img[i][ptr] = or_img[i][j]
                ptr += 1
    return out_img

def fast_seam_carve_add(img, perc, energy_function, vspace, hspace):
    or_img = np.copy(img)
    rem = np.zeros_like(img, dtype=np.int64)
    # print(delmask)
    for i in range(img.shape[0]):
        for j in range(img.shape[1]):
            rem[i][j][0] = j
    # show(rem)
    nops = img.shape[1] * perc // 100
    for i in range(nops):
        mask = fast_get_seam(img, vspace, hspace, energy_function)[1]
        img = remove_seam(img, mask)
        rem = remove_seam(rem, mask)
    out_img = np.empty((or_img.shape[0], or_img.shape[1] + nops, 3), dtype=np.int64)
    delmask = np.ones_like(or_img[:,:,0], dtype=np.bool8)
    # print(delmask.shape)
    # show(rem)
    cnt = 0
    for i in range(or_img.shape[0]):
        cnt = 0
        for j in rem[i, :, 0]:
            cnt += 1
            delmask[i][j] = False
        # print(i, cnt)
    for i in range(or_img.shape[0]):
        ptr = 0
        for j in range(or_img.shape[1]):
            # print(ptr)
            out_img[i][ptr] = or_img[i][j]
            ptr += 1
            if delmask[i][j] == True:
                out_img[i][ptr] = or_img[i][j]
                ptr += 1
    return out_img

def kmeans_fast_seam_carve_add(img, perc, energy_function, clusters, vspace, hspace):
    kimg = kmeans(img, clusters)
    or_img = np.copy(img)
    rem = np.zeros_like(img, dtype=np.int64)
    # print(delmask)
    for i in range(img.shape[0]):
        for j in range(img.shape[1]):
            rem[i][j][0] = j
    # show(rem)
    nops = img.shape[1] * perc // 100
    for i in range(nops):
        mask = fast_get_seam(kimg, vspace, hspace, energy_function)[1]
        kimg = remove_seam(kimg, mask)
        img = remove_seam(img, mask)
        rem = remove_seam(rem, mask)
    out_img = np.empty((or_img.shape[0], or_img.shape[1] + nops, 3), dtype=np.int64)
    delmask = np.ones_like(or_img[:,:,0], dtype=np.bool8)
    # print(delmask.shape)
    # show(rem)
    cnt = 0
    for i in range(or_img.shape[0]):
        cnt = 0
        for j in rem[i, :, 0]:
            cnt += 1
            delmask[i][j] = False
        # print(i, cnt)
    for i in range(or_img.shape[0]):
        ptr = 0
        for j in range(or_img.shape[1]):
            # print(ptr)
            out_img[i][ptr] = or_img[i][j]
            ptr += 1
            if delmask[i][j] == True:
                out_img[i][ptr] = or_img[i][j]
                ptr += 1
    return out_img

In [11]:
def wb_sf(bimg, n1, m1, n2, m2, ms, mf):
    m1 = max(m1, 0)
    m2 = min(m2, bimg.shape[1] - 1)
    img = bimg[n1:(n2 + 1), m1:(m2 + 1)]
    ms -= m1
    mf -= m1
    height, width = img.shape[0], img.shape[1]
    # print(height, width)
    # print(bimg)
    # print(img)
    energies = forward_energy(img)
    sums = np.empty((height, width))
    for i in range(height):
        for j in range(width):
            if abs(j - ms) <= i:
                u, ul, ur = 100000, 100000, 100000
                if i > 0:
                    u = sums[i - 1, j]
                    if j > 0:
                        ul = sums[i - 1, j - 1]
                    if j < width - 1:
                        ur = sums[i - 1, j + 1]
                if i == 0 and j == ms:
                    u, ul, ur = 0, 0, 0
                sums[i, j] = energies[i, j] + min(u, ul, ur)
            else:
                sums[i, j] = 100000
    mask = np.ones((height, width), dtype=bool)
    seam = np.ones((height))
    i, j = height - 1, mf
    for i in range(height - 1, -1, -1):
        mask[i, j] = False
        seam[i] = j
        u, ul, ur = 100000, 100000, 100000
        u = sums[i - 1, j] # without condition
        if j > 0:
            ul = sums[i - 1, j - 1]
        if j < width - 1:
            ur = sums[i - 1, j + 1]
        mini = min(u, ul, ur)
        if mini == ul:
            j -= 1
        if mini == ur:
            j += 1
    mask[0, ms] = False
    #seam = np.append(seam, ms)
    #show_energies(sums)
    #show_energies(mask)
    #show(img)
    return seam, mask

def wb_n(bimg, n1, m1, n2, m2, ms):
    m1 = max(m1, 0)
    m2 = min(m2, bimg.shape[1] - 1)
    img = bimg[n1:(n2 + 1), m1:(m2 + 1)]
    ms -= m1
    height, width = img.shape[0], img.shape[1]
    # print(height, width)
    energies = forward_energy(img)
    sums = np.empty((height, width), dtype=np.int64)
    for i in range(height):
        for j in range(width):
            if abs(j - ms) <= i:
                u, ul, ur = 100000, 100000, 100000
                if i > 0:
                    u = sums[i - 1, j]
                    if j > 0:
                        ul = sums[i - 1, j - 1]
                    if j < width - 1:
                        ur = sums[i - 1, j + 1]
                if i == 0 and j == ms:
                    u, ul, ur = 0, 0, 0
                sums[i, j] = energies[i, j] + min(u, ul, ur)
            else:
                sums[i, j] = 100000
    mask = np.ones((height, width), dtype=bool)
    seam = np.ones((height))
    i, j = height - 1, np.argmin(sums[height - 1,:])
    for i in range(height - 1, -1, -1):
        mask[i, j] = False
        seam[i] = j
        u, ul, ur = 100000, 100000, 100000
        u = sums[i - 1, j] # without condition
        if j > 0:
            ul = sums[i - 1, j - 1]
        if j < width - 1:
            ur = sums[i - 1, j + 1]
        mini = min(u, ul, ur)
        if mini == ul:
            j -= 1
        if mini == ur:
            j += 1
    mask[0, ms] = False
    #seam = np.append(seam, ms)
    #show_energies(sums)
    #show_energies(mask)
    #show(img)
    return seam, mask

In [12]:
def lessen(img, vspace, hspace):
    height, width = img.shape[:2]
    ah = (((height // vspace) * vspace) != height)
    aw = (((width // hspace) * hspace) != width)
    out = np.empty((height // vspace + ah, width // hspace + aw, 3), dtype=np.uint8)
    # print(height, width, height // vspace + ah, width // hspace + aw, ah, aw)
    # print(out) # debug
    # print(out.shape)
    for i in range(height // vspace + ah):
        for j in range(width // hspace + aw):
            out[i, j] = img[i * vspace, j * hspace]
    return out

def get_lessen_grid(img, vspace, hspace):
    height, width = img.shape[:2]
    ah = (((height // vspace) * vspace) != height)
    aw = (((width // hspace) * hspace) != width)
    out = np.copy(img)
    for i in range(height // vspace + ah):
        for j in range(width // hspace + aw):
            out[i * vspace, j * hspace] = [0, 0, 255]
    return out


def fast_get_seam(img, vspace, hspace, energy_function):
    limg = lessen(img, vspace, hspace)
    # show(limg)
    lseam, lmask = get_seam(limg, forward_energy)
    seam = np.array([], dtype=np.int64)
    mask = np.ones(img.shape[:2], dtype=bool)
    # print(len(lseam))
    for i in range(len(lseam) - 1):
        n1 = i * vspace
        n2 = (i + 1) * vspace
        ms = lseam[i] * hspace
        mf = lseam[i + 1] * hspace
        m1, m2 = 0, 0
        if (ms != mf):
            m1 = min(ms, mf) - hspace // 2
            m2 = max(ms, mf) + hspace // 2
        else:
            m1 = ms - hspace // 2
            m2 = ms + hspace // 2
        # print(n1, m1, n2, m2, ms, mf)
        # print(np.array([max(m1, 0)] * (vspace + 1)))
        iseam = wb_sf(img, n1, m1, n2, m2, ms, mf)[0] + np.array([max(m1, 0)] * (vspace + 1))
        # print(iseam)
        seam = np.concatenate((seam, iseam[:-1]))
    i = len(lseam) - 1
    n1 = i * vspace
    m1 = 0
    n2 = img.shape[0] - 1
    m2 = img.shape[1] - 1
    ms = lseam[i] * hspace
    # print(n1, m1, n2, m2, ms)
    iseam = wb_n(img, n1, m1, n2, m2, ms)[0] + np.array([max(m1, 0)] * (n2 - n1 + 1))
#     print(iseam)
    seam = np.concatenate((seam, iseam))

    seam = seam.astype(np.int64)
    # print(len(seam))
    for i in range(len(seam)):
        mask[i, seam[i]] = 0
    return seam, mask

def get_fast_seam_dots(img, vspace, hspace, energy_function):
    limg = lessen(img, vspace, hspace)
    lseam = get_seam(limg, forward_energy)[0]
    cimg = np.copy(img)
    for i in range(lseam.size):
        cimg[i * vspace, lseam[i] * hspace] = [0, 0, 255]
    return cimg

In [18]:
def random_remove(img):
    percent = random.randint(10, 80)
    efunction = random.choice([forward_energy, backward_energy])
    clusters = random.randint(5, 25)
    hspace = random.randint(4, 20)
    vspace = random.randint(hspace, 20)
    
    start = time.process_time()
    rimg = seam_carve_remove(img, percent, efunction)
    tim = time.process_time() - start
    
    start = time.process_time()
    kimg = kmeans_fast_seam_carve_remove(img, percent, efunction, clusters, vspace, hspace)
    ktim = time.process_time() - start
    
    fchoice = {
        forward_energy: "forward_energy",
        backward_energy: "backward_energy"
    }
    report = {
        "action": "remove",
        "percent": percent,
        "efunction": fchoice[efunction],
        "clusters": clusters,
        "vspace": vspace,
        "hspace": hspace,
        "time": tim,
        "ktime": ktim,
    }
    
    return rimg, kimg, report

def random_add(img):
    percent = random.randint(10, 80)
    efunction = random.choice([forward_energy, backward_energy])
    clusters = random.randint(5, 25)
    hspace = random.randint(4, 20)
    vspace = random.randint(hspace, 20)
    
    start = time.process_time()
    rimg = seam_carve_add(img, percent, efunction)
    tim = time.process_time() - start
    
    start = time.process_time()
    kimg = kmeans_fast_seam_carve_add(img, percent, efunction, clusters, vspace, hspace)
    ktim = time.process_time() - start
    
    fchoice = {
        forward_energy: "forward_energy",
        backward_energy: "backward_energy"
    }
    report = {
        "action": "add",
        "percent": percent,
        "efunction": fchoice[efunction],
        "clusters": clusters,
        "vspace": vspace,
        "hspace": hspace,
        "time": tim,
        "ktime": ktim,
    }
    
    return rimg, kimg, report

In [24]:
def process_all_remove(path, opath):
    files = [f for f in listdir(path) if isfile(join(path, f))]
    names = [f.split(".")[0] for f in files]
    for file, name in zip(files, names):
        img = cv2.imread(f"{path}/{file}", 1)
        rimg, kimg, report = random_remove(img)
        odir = f"{opath}/{name}"
        Path(odir).mkdir(parents=True, exist_ok=True)
        cv2.imwrite(f"{odir}/{name}.jpg", img)
        cv2.imwrite(f"{odir}/{name}r.jpg", rimg)
        cv2.imwrite(f"{odir}/{name}k.jpg", kimg)
        repfile = open(f"{odir}/{name}.json", 'w+')
        repfile.write(json.dumps(report))
        repfile.close()

def process_all_add(path, opath):
    files = [f for f in listdir(path) if isfile(join(path, f))]
    names = [f.split(".")[0] for f in files]
    for file, name in zip(files, names):
        img = cv2.imread(f"{path}/{file}", 1)
        rimg, kimg, report = random_add(img)
        odir = f"{opath}/{name}"
        Path(odir).mkdir(parents=True, exist_ok=True)
        cv2.imwrite(f"{odir}/{name}.jpg", img)
        cv2.imwrite(f"{odir}/{name}r.jpg", rimg)
        cv2.imwrite(f"{odir}/{name}k.jpg", kimg)
        repfile = open(f"{odir}/{name}.json", 'w+')
        repfile.write(json.dumps(report))
        repfile.close()
        
def process_all_random(path, opath):
    files = [f for f in listdir(path) if isfile(join(path, f))]
    names = [f.split(".")[0] for f in files]
    for file, name in zip(files, names):
        img = cv2.imread(f"{path}/{file}", 1)
        k = random.randint(0, 1)
        rimg, kimg, report = 0, 0, 0
        if k == 1:
            rimg, kimg, report = random_add(img)
        else:
            rimg, kimg, report = random_remove(img)
        odir = f"{opath}/{name}"
        Path(odir).mkdir(parents=True, exist_ok=True)
        cv2.imwrite(f"{odir}/{name}.jpg", img)
        cv2.imwrite(f"{odir}/{name}r.jpg", rimg)
        cv2.imwrite(f"{odir}/{name}k.jpg", kimg)
        repfile = open(f"{odir}/{name}.json", 'w+')
        repfile.write(json.dumps(report))
        repfile.close()

In [25]:
# HSPACE = 5
# VSPACE = 8
PERCENT = 20
CLUSTERS = 20
EFUNCTION = forward_energy

PATH = "/home/heorhii/man/random_images/"

process_all_random("/home/heorhii/man/random_images/", "/home/heorhii/man/random_images/results/")

In [16]:
# %time res = seam_carve_remove(img, PERCENT, EFUNCTION)
# show(res)

In [17]:
# %time kres = kmeans_fast_seam_carve_remove(img, PERCENT, EFUNCTION, CLUSTERS)
# show(kres)